# 흑백요리사 식당 300m 격자 및 행정동 경계 시각화

이 노트북은 다음 작업을 수행합니다.
1. **300m 격자 생성**: 식당 위치 기준 반경 300m
2. **행정동 경계 로드**: 보유한 SHP 파일을 활용하여 지도에 오버레이
3. **시각화**: Folium (격자 + 행정동)

In [1]:
import geopandas as gpd
import pandas as pd
import folium
from shapely.geometry import Point
import os

In [ ]:
# 1. 식당 데이터 (CSV)
csv_path = r"c:\Users\USER\Documents\웅진씽크빅kdt\흑백요리사\캐치테이블_가게정보.csv"

# 2. 행정동 경계 데이터 (SHP)
shp_path = r"c:\Users\USER\Documents\웅진씽크빅kdt\흑백요리사\(B031)국가기본공간정보()_NF_A_G01106\NF_A_G01106.shp"

# 경로 확인
print(f"CSV Exist: {os.path.exists(csv_path)}")
print(f"SHP Exist: {os.path.exists(shp_path)}")

CSV Exist: True
SHP Exist: True


In [ ]:
def create_300m_grid(df, lat_col, lon_col):
    # Point 변환
    geometry = [Point(xy) for xy in zip(df[lon_col], df[lat_col])]
    gdf = gpd.GeoDataFrame(df, geometry=geometry, crs="EPSG:4326")
    
    # 좌표계 변환 및 버퍼 (300m)
    gdf_proj = gdf.to_crs(epsg=5179)
    gdf_proj['grid_geometry'] = gdf_proj.geometry.buffer(300).envelope
    
    gdf_grid = gdf_proj.set_geometry('grid_geometry')
    gdf_grid = gdf_grid.drop(columns=['geometry'], errors='ignore')
    gdf_grid = gdf_grid.rename_geometry('geometry')
    return gdf_grid

# 실행
df = pd.read_csv(csv_path)
gdf_grid = create_300m_grid(df, 'lat', 'lon')
gdf_grid['area_m2'] = gdf_grid.geometry.area
print("✅ 300m 격자 생성 완료")

✅ 300m 격자 생성 완료


In [ ]:
try:
    # SHP 파일 읽기 (인코딩 주의: cp949)
    print("📂 행정동 SHP 로딩 중...")
    gdf_adm = gpd.read_file(shp_path, encoding='cp949')
    
    # 좌표계 확인 및 변환 (Folium용 WGS84)
    if gdf_adm.crs is None:
        # 좌표계 정보가 없는 경우, 보통 한국은 EPSG:5174 or 5179인데...
        # 일단 5174(Bessel)나 5179일 확률이 높음. 원본 확인 필요.
        # 여기선 에러 방지를 위해 User에게 확인 요청 메시지 출력
        print("⚠️ 경고: SHP 파일에 좌표계(CRS) 정보가 없습니다. 지도에 표시되지 않을 수 있습니다.")
        # 임시로 5179로 가정해봅니다.
        gdf_adm.set_crs(epsg=5179, inplace=True)
    
    gdf_adm_viz = gdf_adm.to_crs(epsg=4326)
    
    print(f"✅ 행정동 데이터 로드 완료: {len(gdf_adm_viz)}개 구역")
    display(gdf_adm_viz.head(3))
    
except Exception as e:
    print(f"❌ SHP 로드 실패: {e}")
    gdf_adm_viz = None

📂 행정동 SHP 로딩 중...
✅ 행정동 데이터 로드 완료: 467개 구역


UFID        BJCD NAME    DIVI      SCLS  \
0  1000037608070G01110000000000000001  1111010100  청운동  HJD010  G0018117   
1  1000037608069G01110000000000000002  1111010200  신교동  HJD010  G0018117   
2  1000037608069G01110000000000000003  1111010300  궁정동  HJD010  G0018117   

    Shape_Leng     Shape_Area  \
0  4130.848014  792622.050433   
1  1436.852438   98820.499822   
2  1388.898508   73270.204787   

                                            geometry  
0  POLYGON ((126.97093 37.59384, 126.97098 37.593...  
1  POLYGON ((126.96851 37.58588, 126.96856 37.585...  
2  POLYGON ((126.97398 37.58653, 126.974 37.58654...

In [ ]:
# 시각화 준비
gdf_grid_viz = gdf_grid.to_crs(epsg=4326)
center_lat = gdf_grid_viz.geometry.centroid.y.mean()
center_lon = gdf_grid_viz.geometry.centroid.x.mean()

m = folium.Map(location=[center_lat, center_lon], zoom_start=12)

# 1. 행정동 경계 레이어 (검은색 실선)
if gdf_adm_viz is not None:
    folium.GeoJson(
        gdf_adm_viz,
        name='행정동 경계',
        style_function=lambda x: {'fillColor': 'none', 'color': 'gray', 'weight': 2, 'dashArray': '5, 5'},
        tooltip=folium.GeoJsonTooltip(fields=list(gdf_adm_viz.columns)[:3]) # 앞 3개 컬럼 툴팁 표시
    ).add_to(m)

# 2. 300m 격자 레이어 (파란색)
folium.GeoJson(
    gdf_grid_viz,
    name='300m Grid',
    style_function=lambda x: {'fillColor': 'blue', 'color': 'blue', 'weight': 1, 'fillOpacity': 0.3},
    tooltip=folium.GeoJsonTooltip(fields=['restaurant', 'area_m2'])
).add_to(m)

folium.LayerControl().add_to(m)
m

C:\Users\USER\AppData\Local\Temp\ipykernel_27456\3377059787.py:3: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  center_lat = gdf_grid_viz.geometry.centroid.y.mean()
C:\Users\USER\AppData\Local\Temp\ipykernel_27456\3377059787.py:4: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  center_lon = gdf_grid_viz.geometry.centroid.x.mean()


1그래프 식당이 어느 지역에 많은 지 행정구별로 히트맵
2그래프 500m격자 안에 유동인구 히트맵

그리고 커서 올리면 리뷰수 나오도록